# Day 13: Care Package
As you ponder the solitude of space and the ever-increasing three-hour roundtrip for messages between you and Earth, you notice that the Space Mail Indicator Light is blinking. To help keep you sane, the Elves have sent you a care package.

It's a new game for the ship's arcade cabinet! Unfortunately, the arcade is all the way on the other end of the ship. Surely, it won't be hard to build your own - the care package even comes with schematics.

The arcade cabinet runs Intcode software like the game the Elves sent (your puzzle input). It has a primitive screen capable of drawing square tiles on a grid. The software draws tiles to the screen with output instructions: every three output instructions specify the x position (distance from the left), y position (distance from the top), and tile id. The tile id is interpreted as follows:

- 0 is an empty tile. No game object appears in this tile.
- 1 is a wall tile. Walls are indestructible barriers.
- 2 is a block tile. Blocks can be broken by the ball.
- 3 is a horizontal paddle tile. The paddle is indestructible.
- 4 is a ball tile. The ball moves diagonally and bounces off objects.

For example, a sequence of output values like 1,2,3,6,5,4 would draw a horizontal paddle tile (1 tile from the left and 2 tiles from the top) and a ball tile (6 tiles from the left and 5 tiles from the top).

Start the game. How many block tiles are on the screen when the game exits?

In [1]:
from intcode import *

In [2]:
import tools

In [3]:
program = make_tape(tools.get_data(13))

In [4]:
def output_structure_state(structure):
    data = []
    for name, type in structure.__annotations__.items():
        datum = yield
        data.append(type(datum))
    yield structure(*data)

In [7]:
def input_structure_state(structure, value):
    for name, datum in zip(structure.__annotations__, value):
        yield int(datum)

In [20]:
class StructuredEnv:
    INPUT_STRUCTURE = None
    OUTPUT_STRUCTURE = None
    
    def __init__(self, initial_input=None):
        self._initial_input = initial_input
        
    def reset(self):
        if self._initial_input:
            self.send(self._initial_input)
        else:
            self.input_state = None
        self.reset_output()
        
    def reset_output(self):
        self._output_state = output_structure_state(self.OUTPUT_STRUCTURE)
        next(self._output_state)  # kick
        
    def input(self):
        if self._input_state is None:
            raise Exception("No input to consume")
        try:
            return self._input_state.next()
        except StopIteration:
            self._input_state = None
            return self.input()
    
    def output(self, value):
        try:
            result = self._output_state.send(value)
            if result is not None:
                self.emit(result)
        except StopIteration:
            self.reset_output()
            return self.output(value)
    
    def emit(self, value):
        raise NotImplemented
        
    def send(self, value):
        self._input_state = input_structure_state(self.INPUT_STRUCTURE, value)

In [8]:
import typing
import enum

class ArcadeBlock(enum.Enum):
    EMPTY = 0
    WALL = 1
    BLOCK = 2
    PADDLE = 3
    BALL = 4

class ArcadeOutput(typing.NamedTuple):
    x: int
    y: int
    block: ArcadeBlock

In [21]:
class ViewArcadeGame(StructuredEnv):
    OUTPUT_STRUCTURE = ArcadeOutput
        
    def reset(self):
        super().reset()
        self.screen = {}
        
    def emit(self, value: ArcadeOutput):
        self.screen[(value.x, value.y)] = value.block

In [22]:
game_state = interpreter.evaluate(program, env=ViewArcadeGame()).env

In [24]:
import collections

In [26]:
collections.Counter(game_state.screen.values())

Counter({<ArcadeBlock.WALL: 1>: 79,
         <ArcadeBlock.EMPTY: 0>: 486,
         <ArcadeBlock.BLOCK: 2>: 247,
         <ArcadeBlock.BALL: 4>: 1,
         <ArcadeBlock.PADDLE: 3>: 1})

# Part Two
The game didn't run because you didn't put in any quarters. Unfortunately, you did not bring any quarters. Memory address 0 represents the number of quarters that have been inserted; set it to 2 to play for free.

The arcade cabinet has a joystick that can move left and right. The software reads the position of the joystick with input instructions:

- If the joystick is in the neutral position, provide 0.
- If the joystick is tilted to the left, provide -1.
- If the joystick is tilted to the right, provide 1.

The arcade cabinet also has a segment display capable of showing a single number that represents the player's current score. When three output instructions specify X=-1, Y=0, the third output instruction is not a tile; the value instead specifies the new score to show in the segment display. For example, a sequence of output values like -1,0,12345 would show 12345 as the player's current score.

Beat the game by breaking all the blocks. What is your score after the last block is broken?

In [27]:
hacked_program = [2] + program[1:]

In [37]:
SCREEN_X, SCREEN_Y = max(game_state.screen)[0] + 1, max(game_state.screen, key=lambda p: p[1])[1] + 1

In [38]:
SCREEN_X, SCREEN_Y

(37, 22)

In [52]:
def game_output_state():
    data = []
    for _ in range(3):
        data.append((yield))
    if data[0:2] == [-1, 0]:
        yield ArcadeScore(data[2])
    else:
        yield ArcadeOutput(data[0], data[1], ArcadeBlock(data[2]))

In [54]:
class ArcadeScore(typing.NamedTuple):
    score: int

In [57]:
class PlayArcadeGame(StructuredEnv):
    BLOCK_ICONS = {
        ArcadeBlock.EMPTY: ' ',
        ArcadeBlock.WALL: '#',
        ArcadeBlock.BLOCK: '.',
        ArcadeBlock.PADDLE: '=',
        ArcadeBlock.BALL: 'O',
    }

    def reset(self):
        super().reset()
        self.screen = {}
        self.score = None
        self.joystick_position = 0
        self.ball_position = (0, 0)
        self.paddle_position = (0, 0)

    def reset_output(self):
        self._output_state = game_output_state()
        next(self._output_state)  # kick

    def emit(self, value: ArcadeOutput):
        if isinstance(value, ArcadeScore):
            self.score = value.score
            print(f'Score: {self.score}')
        else:
            self.screen[(value.x, value.y)] = value.block
            if value.block is ArcadeBlock.PADDLE:
                self.paddle_position = (value.x, value.y)
            elif value.block is ArcadeBlock.BALL:
                self.ball_position = (value.x, value.y)

    def input(self):
        self.refresh_screen()
        # Follow the ball
        bx, _ = self.ball_position
        px, _ = self.paddle_position
        return 1 if px < bx else -1 if px > bx else 0

    def refresh_screen(self):
        for y in range(0, SCREEN_Y):
            row = ''
            for x in range(0, SCREEN_X):
                block = self.screen.get((x, y), ArcadeBlock.EMPTY)
                row += self.BLOCK_ICONS[block]
            print(row)
        print()

interpreter = IntcodeInterpreter()
interpreter.evaluate(hacked_program, env=PlayArcadeGame())

Score: 0
#####################################
#                                   #
# .... ..    .. .....  . . ... .... #
# ....... ...  . .... .. ..   .  .  #
#  . .     .   .  .....   ...   ... #
# ..   ..  ... ..   ... .. .  .. .. #
# . .. . ...  .    ...  .   .   .   #
# .  .. .            .    ..  ....  #
# ..  .  .     . ..... .   .. ..  . #
# . .  .. ...  .........   ..  .... #
# .    .    ...  ... .      ...  .. #
# . ...   .  . .. ..   . .. .. ...  #
# ...  . . ..  .   ... .  .... ...  #
#    . ...... .. .   ....... .    . #
#  . . ....... .  .   ...  .. ..  . #
#   .    .     . ....... . . ...... #
#                                   #
#               O                   #
#                                   #
#                                   #
#                 =                 #
#                                   #

#####################################
#                                   #
# .... ..    .. .....  . . ... .... #
# ....... ...  . .... .. ..   .  .  #
# 

#####################################
#                                   #
# .... ..    .. .....  . . ... .... #
# ....... ...  . .... .. ..   .  .  #
#  . .     .   .  .....   ...   ... #
# ..   ..  ... ..   ... .. .  .. .. #
# . .. . ...  .    ...  .   .   .   #
# .  .. .            .    ..  ....  #
# ..  .  .     . ..... .   .. ..  . #
# . .  .. ...  .........   ..  .... #
# .    .    ...  ... .      ...  .. #
# . ...   .  . .. ..   . .. .. ...  #
# ...  . . ..  .   ... .  .... ...  #
#    . ...... .. .   ....... .    . #
#    . .....   .  .   ...  .. ..  . #
#        .     . .. . ..     .. . . #
#                                   #
#                                   #
#      O                            #
#                                   #
#     =                             #
#                                   #

#####################################
#                                   #
# .... ..    .. .....  . . ... .... #
# ....... ...  . .... .. ..   .  .  #
#  . .     

#####################################
#                                   #
# .... ..    .. .....  . . ... .... #
# ....... ...  . .... .. ..   .  .  #
#  . .     .   .  .....   ...   ... #
# ..   ..  ... ..   ... .. .  .. .. #
# . .. . ...  .    ...  .   .   .   #
# .  .. .            .    ..  ....  #
# ..  .  .     . ..... .   .. ..  . #
# . .  .. ...  .........   ..  .... #
# .    .    ...  ... .      ...  .. #
# . ...   .  . .. ..   . .. .. ...  #
#  ..  . . .   .   ... .  .... ...  #
#    . ....    . .   ....... .    . #
#    . .....   .  .    ..  .. ..  . #
#             O  .. .        .. . . #
#                                   #
#                                   #
#                                   #
#                                   #
#            =                      #
#                                   #

#####################################
#                                   #
# .... ..    .. .....  . . ... .... #
# ....... ...  . .... .. ..   .  .  #
#  . .     

#####################################
#                                   #
# .... ..    .. .....  . . ... .... #
# ....... ...  . .... .. ..   .  .  #
#  . .     .   .  .....   ...   ... #
# ..   ..  ... ..   ... .. .  .. .. #
# . .. . ...  .    ...  .   .   .   #
# .  .. .            .    ..  ....  #
# ..  .  .     . ..... .   .. ..  . #
# . .  .. ...  .........   ..  .... #
# .    .    ...  ... .      ...  .. #
# . ...      . .. ..   . .. .. ...  #
#  ..  . .     .   ... .  .... ...  #
#    . ....    . .   ..  ... .    . #
#    . .....   .  .        .. ..  . #
#                .. .        .. . . #
#                                   #
#               O                   #
#                                   #
#                                   #
#                =                  #
#                                   #

#####################################
#                                   #
# .... ..    .. .....  . . ... .... #
# ....... ...  . .... .. ..   .  .  #
#  . .     

Score: 2577
#####################################
#                                   #
# .... ..    .. .....  . . ... .... #
# ....... ...  . .... .. ..   .  .  #
#  . .     .   .  .....   ...   ... #
# ..   ..  ... ..   ...    .  .. .. #
# . .. . ...  .    ...      .   .   #
# .  .. .            .    O   ....  #
# ..  .  .     . ..... .    . ..  . #
# . .  .  ...  ........    ..  .... #
# .    .    ...  ... .      ...  .. #
# . ...      . .. ..      . .. ...  #
#  ..  . .     .   .      .... ...  #
#    . ....    . .        .. .    . #
#    . .....   .  .        .. ..  . #
#                .. .        .. .   #
#                                   #
#                                   #
#                                   #
#                                   #
#                        =          #
#                                   #

#####################################
#                                   #
# .... ..    .. .....  . . ... .... #
# ....... ...  . .... .. ..   .  .  #

...

#                                   #
#               =                   #
#                                   #

#####################################
#                                   #
# .                                 #
# .                                 #
#                                .  #
#                                   #
#                                   #
#                 O                 #
#                                   #
#                                   #
#                                   #
#                                   #
#                                   #
#                                   #
#                                   #
#                                   #
#                                   #
#                                   #
#                                   #
#                                   #
#                =                  #
#                                   #

#####################################
#         

#####################################
#                                   #
# .                                 #
# .                                 #
#                                .  #
#                                   #
#                                   #
#                                   #
#                                   #
#                                   #
#                  O                #
#                                   #
#                                   #
#                                   #
#                                   #
#                                   #
#                                   #
#                                   #
#                                   #
#                                   #
#                 =                 #
#                                   #

#####################################
#                                   #
# .                                 #
# .                                 #
#          

#####################################
#                                   #
# .                                 #
# .                                 #
#                                .  #
#                                   #
#                                   #
#                                   #
#                                   #
#                                   #
#                                   #
#                                   #
#                                   #
#                   O               #
#                                   #
#                                   #
#                                   #
#                                   #
#                                   #
#                                   #
#                  =                #
#                                   #

#####################################
#                                   #
# .                                 #
# .                                 #
#          

#####################################
#                                   #
#                                   #
# .                                 #
#                                .  #
#                                   #
#                                   #
#                                   #
#                                   #
#                                   #
#                                   #
#                                   #
#                                   #
#                           O       #
#                                   #
#                                   #
#                                   #
#                                   #
#                                   #
#                                   #
#                          =        #
#                                   #

#####################################
#                                   #
#                                   #
# .                                 #
#          


            InterpreterContext(
                index=450,
                state=99,
                relative_base=2271,
                tape=Tape[2, 380, 379, 385, 1008, 2267, 709926, 381, 1005, 381, 12, 99, 109, 2268, 1101, 0, 0, 383, 1101, 0, 0, 382, 20101, 0, 382, 1, 21002, 383, 1, 2, 21102, 37, 1, 0, 1105, 1, 578, 4, 382, 4, 383, 204, 1, 1001, 382, 1, 382, 1007, 382, 37, 381, 1005, 381, 22, 1001, 383, 1, 383, 1007, 383, 22, 381, 1005, 381, 18, 1006, 385, 69, 99, 104, -1, 104, 0, 4, 386, 3, 384, 1007, 384, 0, 381, 1005, 381, 94, 107, 0, 384, 381, 1005, 381, 108, 1105, 1, 161, 107, 1, 392, 381, 1006, 381, 161, 1101, -1, 0, 384, 1106, 0, 119, 1007, 392, 35, 381, 1006, 381, 161, 1101, 0, 1, 384, 21002, 392, 1, 1, 21102, 1, 20, 2, 21102, 1, 0, 3, 21101, 138, 0, 0, 1106, 0, 549, 1, 392, 384, 392, 21001, 392, 0, 1, 21102, 20, 1, 2, 21101, 3, 0, 3, 21101, 0, 161, 0, 1106, 0, 549, 1101, 0, 0, 384, 20001, 388, 390, 1, 21001, 389, 0, 2, 21102, 180, 1, 0, 1105, 1, 578, 1206, 1, 213, 1208, 1,